(pytest_notebook_by_example)=

# pytest-notebook by example

:::{seealso}
This notebook was rendered with [myst-nb](https://myst-nb.readthedocs.io): {nb-download}`tutorial_intro.ipynb`
:::

## Python API

The principal component of `pytest-notebook` is the
{py:class}`~pytest_notebook.nb_regression.NBRegressionFixture` class,
which is an [attrs](http://www.attrs.org) class, whose parameters can be instantiated or set via attributes.

In [1]:
try:
    # Python <= 3.8
    from importlib_resources import files
except ImportError:
    from importlib.resources import files
from pytest_notebook import example_nbs
from pytest_notebook.nb_regression import NBRegressionFixture

In [2]:
fixture = NBRegressionFixture(exec_timeout=50)
fixture.diff_color_words = False
fixture

NBRegressionFixture(exec_notebook=True, exec_cwd=None, exec_allow_errors=False, exec_timeout=50, coverage=False, cov_config=None, cov_source=None, cov_merge=None, post_processors=('coalesce_streams',), process_resources={}, diff_replace=(), diff_ignore=('/cells/*/outputs/*/traceback',), diff_use_color=True, diff_color_words=False, force_regen=False)

The main method is {py:meth}`~pytest_notebook.nb_regression.NBRegressionFixture.check`, which executes a notebook and compares its initial and final contents.

In [3]:
with files(example_nbs).joinpath("example1.ipynb") as path:
    fixture.check(str(path))

NBRegressionError: 
--- expected
+++ obtained
[34m[1m## replaced /cells/1/execution_count:[0m
[31m-  2
[32m+  1

[0m[34m[1m## modified /cells/2/outputs/0/text:[0m
[36m@@ -1,2 +1,2 @@[m
 hallo1[m
[31m-hallo3[m
[32m+[m[32mhallo2[m

[0m[34m[1m## modified /metadata/language_info/version:[0m
[31m-  3.6.7
[32m+  3.9.18

[0m

To return the results, without raising an exception, use ``raise_errors=False``. This returns a {py:class}`~pytest_notebook.nb_regression.NBRegressionResult` instance.

In [4]:
with files(example_nbs).joinpath("example1.ipynb") as path:
    result = fixture.check(str(path), raise_errors=False)

result

NBRegressionResult(diff_full_length=2,diff_filtered_length=2)

In [5]:
print(result.diff_string)


--- expected
+++ obtained
## replaced /cells/1/execution_count:
-  2
+  1

## modified /cells/2/outputs/0/text:
@@ -1,2 +1,2 @@
 hallo1
-hallo3
+hallo2

## modified /metadata/language_info/version:
-  3.6.7
+  3.9.18




The diff of the notebooks is returned as a list of [nbdime](https://nbdime.readthedocs.io) `DiffEntry` objects.

In [6]:
result.diff_filtered

[{'op': 'patch',
  'key': 'cells',
  'diff': [{'op': 'patch',
    'key': 1,
    'diff': [{'op': 'replace', 'key': 'execution_count', 'value': 1}]},
   {'op': 'patch',
    'key': 2,
    'diff': [{'op': 'patch',
      'key': 'outputs',
      'diff': [{'op': 'patch',
        'key': 0,
        'diff': [{'op': 'patch',
          'key': 'text',
          'diff': [{'op': 'patch',
            'key': 1,
            'diff': [{'op': 'addrange', 'key': 5, 'valuelist': '2'},
             {'op': 'removerange', 'key': 5, 'length': 1}]}]}]}]}]}]},
 {'op': 'patch',
  'key': 'metadata',
  'diff': [{'op': 'patch',
    'key': 'language_info',
    'diff': [{'op': 'patch',
      'key': 'version',
      'diff': [{'op': 'addrange', 'key': 0, 'valuelist': ['3.9.18']},
       {'op': 'removerange', 'key': 0, 'length': 1}]}]}]}]

The notebooks are returned as {py:class}`nbformat.NotebookNode` instances.

In [7]:
result.nb_final

{'cells': [{'cell_type': 'markdown',
   'metadata': {},
   'source': '# Markdown Cell'},
  {'cell_type': 'code',
   'execution_count': 1,
   'metadata': {},
   'outputs': [],
   'source': 'from IPython import display'},
  {'cell_type': 'code',
   'execution_count': 2,
   'metadata': {},
   'outputs': [{'output_type': 'stream',
     'name': 'stdout',
     'text': 'hallo1\nhallo2\n'}],
   'source': "print('hallo1')\nprint('hallo2')"}],
 'metadata': {'kernelspec': {'display_name': 'Python 3',
   'language': 'python',
   'name': 'python3'},
  'language_info': {'name': 'python',
   'version': '3.9.18',
   'mimetype': 'text/x-python',
   'codemirror_mode': {'name': 'ipython', 'version': 3},
   'pygments_lexer': 'ipython3',
   'nbconvert_exporter': 'python',
   'file_extension': '.py'}},
 'nbformat': 4,
 'nbformat_minor': 2}

## pytest fixture

:::{seealso}
    {py:mod}`pytest_notebook.ipy_magic`,
    for the notebook magic used to run pytest in a Jupyter Notebook.
:::

In [8]:
%load_ext pytest_notebook.ipy_magic

A {py:class}`~pytest_notebook.nb_regression.NBRegressionFixture` instance can accessed *via* the {py:func}`~pytest_notebook.plugin.nb_regression` fixture.
This instance will be instatiated with parameters dictated by arguments parsed from the pytest command-line and configuration file(s).

:::{note}
pytest-notebook command-line and configuration file parameter names
are the same as for ``NBRegressionFixture``, but with the prefix ``nb_``.

The command-line parameter takes precedence over the configuration file one.
:::

In [9]:
%%pytest -v --color=yes --disable-warnings --nb-exec-timeout 50

---
[pytest]
nb_diff_color_words = True
---
try:
    # Python <= 3.8
    from importlib_resources import files
except ImportError:
    from importlib.resources import files
from pytest_notebook import example_nbs

def test_notebook(nb_regression):
    with files(example_nbs).joinpath("example1.ipynb") as path:
        nb_regression.check(str(path))

============================= test session starts ==============================
platform linux -- Python 3.9.18, pytest-7.4.3, pluggy-1.3.0 -- /home/docs/checkouts/readthedocs.org/user_builds/pytest-notebook/envs/stable/bin/python
cachedir: .pytest_cache
rootdir: /tmp/tmpekw__z5k
configfile: pytest.ini
plugins: pytest_notebook-0.10.0, anyio-4.1.0, cov-4.1.0
collecting ... collected 1 item

test_ipycell.py::test_notebook FAILED                                    [100%]

=================================== FAILURES ===================================
________________________________ test_notebook _________________________________

nb_regression = NBRegressionFixture(exec_notebook=True, exec_cwd='/home/docs/checkouts/readthedocs.org/user_builds/pytest-notebook/env...place=(), diff_ignore=('/cells/*/outputs/*/traceback',), diff_use_color=True, diff_color_words=True, force_regen=False)

    def test_notebook(nb_regression):
        with files(example_nbs).joinpath("example1.ipynb") as path

FAILED                                    [100%]

=================================== FAILURES ===================================
________________________________ test_notebook _________________________________

nb_regression = NBRegressionFixture(exec_notebook=True, exec_cwd='/home/docs/checkouts/readthedocs.org/user_builds/pytest-notebook/env...place=(), diff_ignore=('/cells/*/outputs/*/traceback',), diff_use_color=True, diff_color_words=True, force_regen=False)

    def test_notebook(nb_regression):
        with files(example_nbs).joinpath("example1.ipynb") as path:
>           nb_regression.check(str(path))
E           pytest_notebook.nb_regression.NBRegressionError: 
E           --- expected
E           +++ obtained
E           ## replaced /cells/1/execution_count:
E           -  2
E           +  1
E           
E           ## modified /cells/2/outputs/0/text:
E           @@ -1,2 +1,2 @@
E           hallo1
E           hallo3hallo2
E           
E           ## modified /metadata/lan

## pytest file collection

{py:meth}`~pytest_notebook.nb_regression.NBRegressionFixture.check` can be run automatically on all notebooks using the pytest collection mechanism.
To activate this feature, set `--nb-test-files` on the command-line, or `nb_test_files = True` in the configuration file.

In [10]:
notebook1_content = files(example_nbs).joinpath("example1_pass.ipynb").read_text()
notebook2_content = files(example_nbs).joinpath("example1.ipynb").read_text()

In [11]:
%%pytest -v --color=yes --disable-warnings --nb-test-files

***
(notebook1_content, "test_notebook1.ipynb")
(notebook2_content, "test_notebook2.ipynb")
***

============================= test session starts ==============================
platform linux -- Python 3.9.18, pytest-7.4.3, pluggy-1.3.0 -- /home/docs/checkouts/readthedocs.org/user_builds/pytest-notebook/envs/stable/bin/python
cachedir: .pytest_cache
rootdir: /tmp/tmpxfh6of0t
plugins: pytest_notebook-0.10.0, anyio-4.1.0, cov-4.1.0
collecting ... collected 2 items

test_notebook1.ipynb::nbregression(test_notebook1) FAILED                [ 50%]
test_notebook2.ipynb::nbregression(test_notebook2) FAILED                [100%]

=================================== FAILURES ===================================
____________________ notebook: nbregression(test_notebook1) ____________________
pytest_notebook.nb_regression.NBRegressionError: 
--- expected
+++ obtained
## modified /metadata/language_info/version:
-  3.6.7
+  3.9.18


____________________ notebook: nbregression(test_notebook2) ____________________
pytest_notebook.nb_regression.NBRegressionError: 
--- expected
+++ obtained
## rep

FAILED                [ 50%]
test_notebook2.ipynb::nbregression(test_notebook2) 

FAILED                [100%]

=================================== FAILURES ===================================
____________________ notebook: nbregression(test_notebook1) ____________________
pytest_notebook.nb_regression.NBRegressionError: 
--- expected
+++ obtained
## modified /metadata/language_info/version:
-  3.6.7
+  3.9.18


____________________ notebook: nbregression(test_notebook2) ____________________
pytest_notebook.nb_regression.NBRegressionError: 
--- expected
+++ obtained
## replaced /cells/1/execution_count:
-  2
+  1

## modified /cells/2/outputs/0/text:
@@ -1,2 +1,2 @@
 hallo1
-hallo3
+hallo2

## modified /metadata/language_info/version:
-  3.6.7
+  3.9.18


=========================== short test summary info ============================
FAILED test_notebook1.ipynb::nbregression(test_notebook1)
FAILED test_notebook2.ipynb::nbregression(test_notebook2)
======================== 2 failed, 2 warnings in 2.95s =========================


In [12]:
%%pytest -v --color=yes --disable-warnings

---
[pytest]
nb_test_files = True
---

***
(notebook1_content, "test_notebook1.ipynb")
(notebook2_content, "test_notebook2.ipynb")
***

============================= test session starts ==============================
platform linux -- Python 3.9.18, pytest-7.4.3, pluggy-1.3.0 -- /home/docs/checkouts/readthedocs.org/user_builds/pytest-notebook/envs/stable/bin/python
cachedir: .pytest_cache
rootdir: /tmp/tmp8jtkn8se
configfile: pytest.ini
plugins: pytest_notebook-0.10.0, anyio-4.1.0, cov-4.1.0
collecting ... collected 2 items

test_notebook1.ipynb::nbregression(test_notebook1) FAILED                [ 50%]
test_notebook2.ipynb::nbregression(test_notebook2) FAILED                [100%]

=================================== FAILURES ===================================
____________________ notebook: nbregression(test_notebook1) ____________________
pytest_notebook.nb_regression.NBRegressionError: 
--- expected
+++ obtained
## modified /metadata/language_info/version:
-  3.6.7
+  3.9.18


____________________ notebook: nbregression(test_notebook2) ____________________
pytest_notebook.nb_regression.NBRegressionError: 
--- expec

FAILED                [ 50%]
test_notebook2.ipynb::nbregression(test_notebook2) 

FAILED                [100%]

=================================== FAILURES ===================================
____________________ notebook: nbregression(test_notebook1) ____________________
pytest_notebook.nb_regression.NBRegressionError: 
--- expected
+++ obtained
## modified /metadata/language_info/version:
-  3.6.7
+  3.9.18


____________________ notebook: nbregression(test_notebook2) ____________________
pytest_notebook.nb_regression.NBRegressionError: 
--- expected
+++ obtained
## replaced /cells/1/execution_count:
-  2
+  1

## modified /cells/2/outputs/0/text:
@@ -1,2 +1,2 @@
 hallo1
-hallo3
+hallo2

## modified /metadata/language_info/version:
-  3.6.7
+  3.9.18


=========================== short test summary info ============================
FAILED test_notebook1.ipynb::nbregression(test_notebook1)
FAILED test_notebook2.ipynb::nbregression(test_notebook2)
======================== 2 failed, 2 warnings in 2.97s =========================


To restrict the notebook files pytest collects, one or more filename pattern matches can also be set (see {py:mod}`fnmatch`).

In [13]:
%%pytest -v --color=yes --disable-warnings

---
[pytest]
nb_test_files = True
nb_file_fnmatch = test_*.ipynb tutorial_*.ipynb
---

***
(notebook1_content, "test_notebook1.ipynb")
(notebook2_content, "other_notebook2.ipynb")
***

============================= test session starts ==============================
platform linux -- Python 3.9.18, pytest-7.4.3, pluggy-1.3.0 -- /home/docs/checkouts/readthedocs.org/user_builds/pytest-notebook/envs/stable/bin/python
cachedir: .pytest_cache
rootdir: /tmp/tmpgb5lmt05
configfile: pytest.ini
plugins: pytest_notebook-0.10.0, anyio-4.1.0, cov-4.1.0
collecting ... collected 1 item

test_notebook1.ipynb::nbregression(test_notebook1) FAILED                [100%]

=================================== FAILURES ===================================
____________________ notebook: nbregression(test_notebook1) ____________________
pytest_notebook.nb_regression.NBRegressionError: 
--- expected
+++ obtained
## modified /metadata/language_info/version:
-  3.6.7
+  3.9.18


=========================== short test summary info ============================
FAILED test_notebook1.ipynb::nbregression(test_notebook1)
========================= 1 failed, 1 warning in 1.73s =========================


FAILED                [100%]

=================================== FAILURES ===================================
____________________ notebook: nbregression(test_notebook1) ____________________
pytest_notebook.nb_regression.NBRegressionError: 
--- expected
+++ obtained
## modified /metadata/language_info/version:
-  3.6.7
+  3.9.18


=========================== short test summary info ============================
FAILED test_notebook1.ipynb::nbregression(test_notebook1)
========================= 1 failed, 1 warning in 1.73s =========================


## Live Logging of Cell Execution

If you wish to view the progress of the notebook execution, you can use the [pytest live-logging](https://docs.pytest.org/en/latest/logging.html#live-logs) functionality:

In [14]:
%%pytest -v --color=yes --disable-warnings --nb-test-files --log-cli-level=info

***
(notebook1_content, "test_notebook1.ipynb")
***

============================= test session starts ==============================
platform linux -- Python 3.9.18, pytest-7.4.3, pluggy-1.3.0 -- /home/docs/checkouts/readthedocs.org/user_builds/pytest-notebook/envs/stable/bin/python
cachedir: .pytest_cache
rootdir: /tmp/tmphw3kqukq
plugins: pytest_notebook-0.10.0, anyio-4.1.0, cov-4.1.0
collecting ... collected 1 item

test_notebook1.ipynb::nbregression(test_notebook1) 
-------------------------------- live log call ---------------------------------
INFO     pytest_notebook.execution:execution.py:97 Executing notebook with kernel: python3
FAILED                                                                   [100%]

=================================== FAILURES ===================================
____________________ notebook: nbregression(test_notebook1) ____________________
pytest_notebook.nb_regression.NBRegressionError: 
--- expected
+++ obtained
## modified /metadata/language_info/version:
-  3.6.7
+  3.9.18


--------------------


-------------------------------- live log call ---------------------------------
INFO     pytest_notebook.execution:execution.py:97 Executing notebook with kernel: python3


FAILED                                                                   [100%]

=================================== FAILURES ===================================
____________________ notebook: nbregression(test_notebook1) ____________________
pytest_notebook.nb_regression.NBRegressionError: 
--- expected
+++ obtained
## modified /metadata/language_info/version:
-  3.6.7
+  3.9.18


------------------------------ Captured log call -------------------------------
INFO     pytest_notebook.execution:execution.py:97 Executing notebook with kernel: python3
=========================== short test summary info ============================
FAILED test_notebook1.ipynb::nbregression(test_notebook1)
========================= 1 failed, 1 warning in 1.72s =========================


(regen_notebooks)=

## Regenerating Notebooks

Failing notebooks can be regenerated by setting `--nb-force-regen`.
This will overwrite failing notebooks with the output from the notebook execution.

:::{note}
Notebooks will not be regenerated if they raise any unexpected exceptions,
during execution.

This approach to regeneration mimics [pytest-regressions](https://pytest-regressions.readthedocs.io).
:::

In [15]:
%%pytest -v --color=yes --disable-warnings --nb-force-regen

---
[pytest]
nb_test_files = True
nb_force_regen = True
---

***
(notebook1_content, "test_notebook1.ipynb")
(notebook2_content, "test_notebook2.ipynb")
***

============================= test session starts ==============================
platform linux -- Python 3.9.18, pytest-7.4.3, pluggy-1.3.0 -- /home/docs/checkouts/readthedocs.org/user_builds/pytest-notebook/envs/stable/bin/python
cachedir: .pytest_cache
NB force regen: True
rootdir: /tmp/tmpp6f8s34h
configfile: pytest.ini
plugins: pytest_notebook-0.10.0, anyio-4.1.0, cov-4.1.0
collecting ... collected 2 items

test_notebook1.ipynb::nbregression(test_notebook1) FAILED                [ 50%]
test_notebook2.ipynb::nbregression(test_notebook2) FAILED                [100%]

=================================== FAILURES ===================================
____________________ notebook: nbregression(test_notebook1) ____________________
pytest_notebook.nb_regression.NBRegressionError: Files differ and --nb-force-regen set, regenerating file at:
- /tmp/tmpp6f8s34h/test_notebook1.ipynb
----------------------------- Captured stderr call -----------------------------
Diff before regeneration:

---

FAILED                [ 50%]
test_notebook2.ipynb::nbregression(test_notebook2) 

FAILED                [100%]

=================================== FAILURES ===================================
____________________ notebook: nbregression(test_notebook1) ____________________
pytest_notebook.nb_regression.NBRegressionError: Files differ and --nb-force-regen set, regenerating file at:
- /tmp/tmpp6f8s34h/test_notebook1.ipynb
----------------------------- Captured stderr call -----------------------------
Diff before regeneration:

--- expected
+++ obtained
## modified /metadata/language_info/version:
-  3.6.7
+  3.9.18


____________________ notebook: nbregression(test_notebook2) ____________________
pytest_notebook.nb_regression.NBRegressionError: Files differ and --nb-force-regen set, regenerating file at:
- /tmp/tmpp6f8s34h/test_notebook2.ipynb
----------------------------- Captured stderr call -----------------------------
Diff before regeneration:

--- expected
+++ obtained
## replaced /cells/1/execution_count:
-  2
+  1

## modified /cells/2/outputs/0/text:
@@ -1,2

The regeneration can be observed, if we run two tests on the same notebook.

In [16]:
%%pytest -v --color=yes --disable-warnings

import os, tempfile
try:
    # Python <= 3.8
    from importlib_resources import files
except ImportError:
    from importlib.resources import files
import pytest
from pytest_notebook import example_nbs

@pytest.fixture(scope="module")
def notebook():
    tmphandle, tmppath = tempfile.mkstemp(suffix=".ipynb")
    with open(tmppath, "w") as handle:
        handle.write(
            files(example_nbs).joinpath("example1.ipynb").read_text()
        )
    yield tmppath
    os.remove(tmppath)

def test_notebook1(nb_regression, notebook):
    nb_regression.force_regen = True
    nb_regression.check(notebook)

def test_notebook2(nb_regression, notebook):
    nb_regression.check(notebook)

============================= test session starts ==============================
platform linux -- Python 3.9.18, pytest-7.4.3, pluggy-1.3.0 -- /home/docs/checkouts/readthedocs.org/user_builds/pytest-notebook/envs/stable/bin/python
cachedir: .pytest_cache
rootdir: /tmp/tmpl8v2ihs9
plugins: pytest_notebook-0.10.0, anyio-4.1.0, cov-4.1.0
collecting ... collected 2 items

test_ipycell.py::test_notebook1 FAILED                                   [ 50%]
test_ipycell.py::test_notebook2 PASSED                                   [100%]

=================================== FAILURES ===================================
________________________________ test_notebook1 ________________________________

nb_regression = NBRegressionFixture(exec_notebook=True, exec_cwd='/tmp', exec_allow_errors=False, exec_timeout=120, coverage=False, co...place=(), diff_ignore=('/cells/*/outputs/*/traceback',), diff_use_color=True, diff_color_words=False, force_regen=True)
notebook = '/tmp/tmpicqnlw9n.ipynb'

    def te

FAILED                                   [ 50%]
test_ipycell.py::test_notebook2 

PASSED                                   [100%]

=================================== FAILURES ===================================
________________________________ test_notebook1 ________________________________

nb_regression = NBRegressionFixture(exec_notebook=True, exec_cwd='/tmp', exec_allow_errors=False, exec_timeout=120, coverage=False, co...place=(), diff_ignore=('/cells/*/outputs/*/traceback',), diff_use_color=True, diff_color_words=False, force_regen=True)
notebook = '/tmp/tmpicqnlw9n.ipynb'

    def test_notebook1(nb_regression, notebook):
        nb_regression.force_regen = True
>       nb_regression.check(notebook)
E       pytest_notebook.nb_regression.NBRegressionError: Files differ and --nb-force-regen set, regenerating file at:
E       - /tmp/tmpicqnlw9n.ipynb

test_ipycell.py:23: NBRegressionError
----------------------------- Captured stderr call -----------------------------
Diff before regeneration:

--- expected
+++ obtained
## replaced /cells/1/execution_count:
-  2